In [41]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import lightgbm as lgb
import optuna
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.metrics import log_loss

In [2]:
data = pd.read_csv('train.csv')
test_data = pd.read_csv('test.csv')

In [8]:
!pip install lightgbm==3.3.5
!pip install optuna==2.10.1

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 22.4 MB/s eta 0:00:00
  Attempting uninstall: lightgbm
    Found existing installation: lightgbm 4.5.0
    Uninstalling lightgbm-4.5.0:
      Successfully uninstalled lightgbm-4.5.0
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 308.2/308.2 kB 7.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 231.9/231.9 kB 18.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.6/84.6 kB 6.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 152.8/152.8 kB 11.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.5/49.5 kB 2.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 109.0/109.0 kB 9.2 MB/s eta 0:00:00


In [3]:

!pip install catboost

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 99.2/99.2 MB 6.5 MB/s eta 0:00:00


In [4]:
X = data.drop(['Status','id'], axis=1)
y = data['Status']

In [5]:
X['Drug'] = X['Drug'].fillna('NA')

X['Ascites'] = X['Ascites'].replace(np.nan, X['Ascites'].mode()[0])  # Replace 'NaN' string

X['Hepatomegaly']= X['Hepatomegaly'].replace( np.nan, X['Hepatomegaly'].mode()[0])  # Replace 'NaN' string

X['Spiders'] =X['Spiders'].replace(np.nan, X['Spiders'].mode()[0])  # Replace 'NaN' string

In [ ]:
# prompt: please train a catboost model

from catboost import CatBoostClassifier
from sklearn.model_selection import train_test_split

X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)

model = CatBoostClassifier(iterations=1000,
                          learning_rate=0.05,
                          depth=6,
                          loss_function='MultiClass',
                          eval_metric='AUC',
                          random_seed=42,
                          verbose=100)

model.fit(X_train, y_train, eval_set=(X_val, y_val), cat_features=["Sex","Ascites","Hepatomegaly","Spiders","Drug","Edema"])


0:	test: 0.8005146	best: 0.8005146 (0)	total: 95.6ms	remaining: 1m 35s
100:	test: 0.8992156	best: 0.8992156 (100)	total: 3.53s	remaining: 31.5s
200:	test: 0.9061516	best: 0.9066927 (196)	total: 6.96s	remaining: 27.6s
300:	test: 0.9096323	best: 0.9099209 (289)	total: 11.9s	remaining: 27.6s
400:	test: 0.9117462	best: 0.9121951 (379)	total: 15.5s	remaining: 23.2s
500:	test: 0.9138427	best: 0.9146432 (489)	total: 19s	remaining: 18.9s
600:	test: 0.9140063	best: 0.9146967 (523)	total: 24.4s	remaining: 16.2s
700:	test: 0.9143562	best: 0.9146967 (523)	total: 27.9s	remaining: 11.9s
800:	test: 0.9140100	best: 0.9149651 (758)	total: 32.3s	remaining: 8.01s
900:	test: 0.9134417	best: 0.9149651 (758)	total: 37.1s	remaining: 4.08s
999:	test: 0.9132473	best: 0.9149651 (758)	total: 40.6s	remaining: 0us

bestTest = 0.9149650945
bestIteration = 758

Shrink model to first 759 iterations.


In [ ]:
# prompt: find logloss of the model using whole data X

from sklearn.metrics import log_loss

y_pred_proba = model.predict_proba(X)
logloss_score = log_loss(y, y_pred_proba)
print(f"Log Loss on the whole dataset: {logloss_score}")


Log Loss on the whole dataset: 0.3078127305058152


In [ ]:
!pip install optuna

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 386.6/386.6 kB 7.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 231.9/231.9 kB 14.5 MB/s eta 0:00:00


In [17]:
import optuna
from catboost import CatBoostClassifier, Pool
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

cat_features=["Sex","Ascites","Hepatomegaly","Spiders","Drug","Edema"]

# Convert categorical features to category dtype
for col in cat_features:
    X_train[col] = X_train[col].astype('category')
    X_val[col] = X_val[col].astype('category')
# Split
X_train, X_valid, y_train, y_valid = train_test_split(X, y, stratify=y, test_size=0.2, random_state=42)

def objective(trial):
    params = {
        'iterations': trial.suggest_int('iterations', 500, 2000),
        'depth': trial.suggest_int('depth', 4, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 1, 10),
        'random_strength': trial.suggest_float('random_strength', 0.1, 2.0),
        'bagging_temperature': trial.suggest_float('bagging_temperature', 0, 1),
        'border_count': trial.suggest_int('border_count', 32, 255),
        'task_type': 'CPU',
        'loss_function': 'MultiClass',
        'eval_metric': 'Accuracy',
        'verbose': 0,
        'early_stopping_rounds': 50
    }

    train_pool = Pool(X_train, y_train, cat_features=cat_features)
    valid_pool = Pool(X_valid, y_valid, cat_features=cat_features)

    model = CatBoostClassifier(**params)
    model.fit(train_pool, eval_set=valid_pool)

    preds = model.predict(X_valid)
    acc = accuracy_score(y_valid, preds)
    return acc  # or use AUC, F1, etc.

# Run Optuna
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=50)

# Best hyperparameters
print("Best trial:")
print(study.best_trial.params)

[I 2025-04-19 07:21:25,064] A new study created in memory with name: no-name-51877566-e9a8-4fed-bb0c-7e40cf9f017d


KeyboardInterrupt: 

In [ ]:
best_params = study.best_trial.params
# Remove 'iterations' from best_params to avoid conflict
del best_params['iterations']
best_model = CatBoostClassifier(**best_params, iterations=study.best_trial.params['iterations'])
best_model.fit(X, y, cat_features=cat_features)

0:	learn: 0.9560350	total: 26.7ms	remaining: 36.5s
1:	learn: 0.8542477	total: 49.7ms	remaining: 34s
2:	learn: 0.7767420	total: 76.2ms	remaining: 34.7s
3:	learn: 0.7175886	total: 99.5ms	remaining: 33.9s
4:	learn: 0.6704834	total: 123ms	remaining: 33.5s
5:	learn: 0.6306659	total: 148ms	remaining: 33.6s
6:	learn: 0.5969812	total: 172ms	remaining: 33.4s
7:	learn: 0.5701046	total: 195ms	remaining: 33.2s
8:	learn: 0.5478599	total: 219ms	remaining: 33.1s
9:	learn: 0.5294783	total: 244ms	remaining: 33.2s
10:	learn: 0.5141170	total: 268ms	remaining: 33.1s
11:	learn: 0.5024224	total: 291ms	remaining: 32.9s
12:	learn: 0.4910156	total: 313ms	remaining: 32.6s
13:	learn: 0.4825248	total: 334ms	remaining: 32.4s
14:	learn: 0.4735150	total: 358ms	remaining: 32.3s
15:	learn: 0.4657869	total: 382ms	remaining: 32.3s
16:	learn: 0.4592765	total: 406ms	remaining: 32.3s
17:	learn: 0.4537469	total: 433ms	remaining: 32.5s
18:	learn: 0.4494549	total: 458ms	remaining: 32.6s
19:	learn: 0.4446325	total: 483ms	remai

In [ ]:
# prompt: find logloss of the model using whole data X

from sklearn.metrics import log_loss

y_pred_proba_best = best_model.predict_proba(X)
logloss_score = log_loss(y, y_pred_proba)
print(f"Log Loss on the whole dataset: {logloss_score}")

Log Loss on the whole dataset: 0.3078127305058152


# LIGHT GBM

In [39]:
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import StratifiedKFold # For cross-validation

X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)
cat_features=["Sex","Ascites","Hepatomegaly","Spiders","Drug","Edema"]

# Convert categorical features to category dtype
for col in cat_features:
    X_train[col] = X_train[col].astype('category')
    X_val[col] = X_val[col].astype('category')


 # Initialize LabelEncoder
label_encoder = LabelEncoder()

# Fit and transform y_train
y_train = label_encoder.fit_transform(y_train)

# Transform y_val using the same encoder
y_val = label_encoder.transform(y_val)



def objective(trial):
    # Define hyperparameters to tune
    params = {
        'objective': 'multiclass',
        'num_class': 3,  # Adjust based on your number of classes
        'metric': 'multi_logloss',
        'boosting_type': 'gbdt',
        'num_leaves': trial.suggest_int('num_leaves', 32, 128),
        'learning_rate': trial.suggest_float('learning_rate', 1e-3, 0.1, log=True),
        'feature_fraction': trial.suggest_float('feature_fraction', 0.5, 1.0),
        'bagging_fraction': trial.suggest_float('bagging_fraction', 0.5, 1.0),
        'bagging_freq': trial.suggest_int('bagging_freq', 1, 10),
        'min_child_samples': trial.suggest_int('min_child_samples', 10, 100),
        'lambda_l1': trial.suggest_float('lambda_l1', 1e-8, 10.0, log=True),
        'lambda_l2': trial.suggest_float('lambda_l2', 1e-8, 10.0, log=True),
        'min_data_in_leaf': trial.suggest_int('min_data_in_leaf', 20, 100),
        'max_depth': trial.suggest_int('max_depth', 5, 15),
    }

     # Cross-validation
    n_splits = 5  # Adjust the number of folds
    skf = StratifiedKFold(n_splits=n_splits, shuffle=True, random_state=42)
    log_loss_scores = []

    for fold, (train_index, valid_index) in enumerate(skf.split(X, y)):
        X_train, X_valid = X.iloc[train_index], X.iloc[valid_index]
        y_train, y_valid = y[train_index], y[valid_index]

        train_data = lgb.Dataset(X_train, label=y_train, categorical_feature=cat_features)
        valid_data = lgb.Dataset(X_valid, label=y_valid, categorical_feature=cat_features)

        model = lgb.train(params, train_data, valid_sets=[valid_data],
                        early_stopping_rounds=100, verbose_eval=False)


        y_pred_proba = model.predict(X_valid, num_iteration=model.best_iteration)
        log_loss_scores.append(log_loss(y_valid, y_pred_proba))

    return np.mean(log_loss_scores)

In [42]:
study = optuna.create_study(direction="minimize", sampler=optuna.samplers.TPESampler()) # Minimize log loss
study.optimize(objective, n_trials=200)

print("Best trial:")
trial = study.best_trial
print(f"  Value: {trial.value}")
print(f"  Params: ")
for key, value in trial.params.items():
    print(f"    {key}: {value}")

[I 2025-04-19 08:08:46,800] A new study created in memory with name: no-name-bd3459a0-f7e6-4f88-9539-f1fec3bbc124
/usr/local/lib/python3.11/dist-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/usr/local/lib/python3.11/dist-packages/lightgbm/basic.py:2065: UserWarning: Using categorical_feature in Dataset.
  _log_warning('Using categorical_feature in Dataset.')
/usr/local/lib/python3.11/dist-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. "
/usr/loca

[LightGBM] [Warning] min_data_in_leaf is set=87, min_child_samples=23 will be ignored. Current value: min_data_in_leaf=87
[LightGBM] [Warning] min_data_in_leaf is set=87, min_child_samples=23 will be ignored. Current value: min_data_in_leaf=87
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000998 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1963
[LightGBM] [Info] Number of data points in the train set: 12000, number of used features: 18
[LightGBM] [Warning] min_data_in_leaf is set=87, min_child_samples=23 will be ignored. Current value: min_data_in_leaf=87
[LightGBM] [Info] Start training from score -0.395515
[LightGBM] [Info] Start training from score -3.722781
[LightGBM] [Info] Start training from score -1.195674
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits wi

/usr/local/lib/python3.11/dist-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/usr/local/lib/python3.11/dist-packages/lightgbm/basic.py:2065: UserWarning: Using categorical_feature in Dataset.
  _log_warning('Using categorical_feature in Dataset.')
/usr/local/lib/python3.11/dist-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. "
/usr/local/lib/python3.11/dist-packages/lightgbm/basic.py:1780: UserWarning: Overriding the parameters from Reference Datas

[LightGBM] [Warning] min_data_in_leaf is set=87, min_child_samples=23 will be ignored. Current value: min_data_in_leaf=87
[LightGBM] [Warning] min_data_in_leaf is set=87, min_child_samples=23 will be ignored. Current value: min_data_in_leaf=87
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000936 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1962
[LightGBM] [Info] Number of data points in the train set: 12000, number of used features: 18
[LightGBM] [Warning] min_data_in_leaf is set=87, min_child_samples=23 will be ignored. Current value: min_data_in_leaf=87
[LightGBM] [Info] Start training from score -0.395391
[LightGBM] [Info] Start training from score -3.722781
[LightGBM] [Info] Start training from score -1.195950
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits wi

/usr/local/lib/python3.11/dist-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/usr/local/lib/python3.11/dist-packages/lightgbm/basic.py:2065: UserWarning: Using categorical_feature in Dataset.
  _log_warning('Using categorical_feature in Dataset.')
/usr/local/lib/python3.11/dist-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. "
/usr/local/lib/python3.11/dist-packages/lightgbm/basic.py:1780: UserWarning: Overriding the parameters from Reference Datas

...

[LightGBM] [Warning] min_data_in_leaf is set=95, min_child_samples=13 will be ignored. Current value: min_data_in_leaf=95
[LightGBM] [Warning] min_data_in_leaf is set=95, min_child_samples=13 will be ignored. Current value: min_data_in_leaf=95
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.011577 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1970
[LightGBM] [Info] Number of data points in the train set: 12000, number of used features: 18
[LightGBM] [Warning] min_data_in_leaf is set=95, min_child_samples=13 will be ignored. Current value: min_data_in_leaf=95
[LightGBM] [Info] Start training from score -0.395391
[LightGBM] [Info] Start training from score -3.726235
[LightGBM] [Info] Start training from score -1.195674
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits wi

/usr/local/lib/python3.11/dist-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/usr/local/lib/python3.11/dist-packages/lightgbm/basic.py:2065: UserWarning: Using categorical_feature in Dataset.
  _log_warning('Using categorical_feature in Dataset.')
/usr/local/lib/python3.11/dist-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. "
/usr/local/lib/python3.11/dist-packages/lightgbm/basic.py:1780: UserWarning: Overriding the parameters from Reference Datas

[LightGBM] [Warning] min_data_in_leaf is set=95, min_child_samples=13 will be ignored. Current value: min_data_in_leaf=95
[LightGBM] [Warning] min_data_in_leaf is set=95, min_child_samples=13 will be ignored. Current value: min_data_in_leaf=95
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001799 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1963
[LightGBM] [Info] Number of data points in the train set: 12000, number of used features: 18
[LightGBM] [Warning] min_data_in_leaf is set=95, min_child_samples=13 will be ignored. Current value: min_data_in_leaf=95
[LightGBM] [Info] Start training from score -0.395391
[LightGBM] [Info] Start training from score -3.726235
[LightGBM] [Info] Start training from score -1.195674
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits wi

[I 2025-04-19 08:46:53,720] Trial 199 finished with value: 0.36944811621336926 and parameters: {'num_leaves': 64, 'learning_rate': 0.07649910421124705, 'feature_fraction': 0.5086916305150637, 'bagging_fraction': 0.9663478260435563, 'bagging_freq': 1, 'min_child_samples': 13, 'lambda_l1': 6.035910827805589e-08, 'lambda_l2': 1.4007328774012484e-07, 'min_data_in_leaf': 95, 'max_depth': 13}. Best is trial 168 with value: 0.3680478716341278.


Best trial:
  Value: 0.3680478716341278
  Params: 
    num_leaves: 61
    learning_rate: 0.07017177302365407
    feature_fraction: 0.5144268443723902
    bagging_fraction: 0.9789478893507481
    bagging_freq: 1
    min_child_samples: 14
    lambda_l1: 1.4546462322663912e-07
    lambda_l2: 1.9043556727586044e-07
    min_data_in_leaf: 93
    max_depth: 13


In [43]:
best_params = trial.params
best_params['objective'] = 'multiclass'  # Add back the objective
best_params['num_class'] = 3  # Add back num_class
best_params['metric'] = 'multi_logloss'  # Add back the metric

cat_features=["Sex","Ascites","Hepatomegaly","Spiders","Drug","Edema"]

# Convert categorical features to category dtype
for col in cat_features:
    X[col] = X[col].astype('category')

y = label_encoder.fit_transform(y)


train_data = lgb.Dataset(X, label=y, categorical_feature=cat_features)  # Use entire data for final training

final_model_lgb = lgb.train(best_params, train_data, num_boost_round=1000)  # Adjust num_boost_round

/usr/local/lib/python3.11/dist-packages/lightgbm/basic.py:2065: UserWarning: Using categorical_feature in Dataset.
  _log_warning('Using categorical_feature in Dataset.')


[LightGBM] [Warning] min_data_in_leaf is set=93, min_child_samples=14 will be ignored. Current value: min_data_in_leaf=93
[LightGBM] [Warning] min_data_in_leaf is set=93, min_child_samples=14 will be ignored. Current value: min_data_in_leaf=93
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001134 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1976
[LightGBM] [Info] Number of data points in the train set: 15000, number of used features: 18
[LightGBM] [Info] Start training from score -0.395416
[LightGBM] [Info] Start training from score -3.724161
[LightGBM] [Info] Start training from score -1.195784
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [W

In [44]:
X_test = pd.read_csv('test.csv')

In [45]:
X_test['Drug'] = X_test['Drug'].fillna('NA')

X_test['Ascites'] = X_test['Ascites'].replace(np.nan, X['Ascites'].mode()[0])  # Replace 'NaN' string

X_test['Hepatomegaly']= X_test['Hepatomegaly'].replace( np.nan, X['Hepatomegaly'].mode()[0])  # Replace 'NaN' string

X_test['Spiders'] =X_test['Spiders'].replace(np.nan, X['Spiders'].mode()[0])  # Replace 'NaN' string

In [46]:
best_params['objective'] = 'multiclass'
best_params['num_class'] = 3  # adjust if needed
best_params['metric'] = 'multi_logloss'  # or other suitable metric

# Ensure categorical features in X_test have the same categories and dtype as X
cat_features = ["Sex", "Ascites", "Hepatomegaly", "Spiders", "Drug", "Edema"]
for col in cat_features:
    X_test[col] = X_test[col].astype(X[col].dtype)  # Match dtype of X
    # Align categories if necessary
    X_test[col] = pd.Categorical(X_test[col], categories=X[col].cat.categories)

# Create LGBMClassifier with best params
model = lgb.LGBMClassifier(**best_params)

# Re-train with the ENTIRE dataset for final predictions
model.fit(X, y, categorical_feature=cat_features)  # X and y are from original training data

# Now, use predict_proba on the X_test dataset
y_pred_proba = model.predict_proba(X_test.drop(['id'], axis=1))

/usr/local/lib/python3.11/dist-packages/lightgbm/basic.py:2065: UserWarning: Using categorical_feature in Dataset.
  _log_warning('Using categorical_feature in Dataset.')


[LightGBM] [Warning] feature_fraction is set=0.5144268443723902, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.5144268443723902
[LightGBM] [Warning] lambda_l1 is set=1.4546462322663912e-07, reg_alpha=0.0 will be ignored. Current value: lambda_l1=1.4546462322663912e-07
[LightGBM] [Warning] bagging_fraction is set=0.9789478893507481, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9789478893507481
[LightGBM] [Warning] lambda_l2 is set=1.9043556727586044e-07, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1.9043556727586044e-07
[LightGBM] [Warning] min_data_in_leaf is set=93, min_child_samples=14 will be ignored. Current value: min_data_in_leaf=93
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1


In [ ]:
catboost_model = []

In [47]:
# prompt: concat X_test id in y_pred_test

import pandas as pd
# Assuming y_pred_test and X_test are defined as in your provided code.

# Create a DataFrame with the predictions
submission_df = pd.DataFrame(y_pred_proba, columns=['Status_C', 'Status_CL','Status_D'])

# Concatenate the 'id' column from X_test to the predictions DataFrame
submission_df['id'] = X_test['id'].values

# Reorder columns to have 'id' as the first column
submission_df = submission_df[['id', 'Status_C', 'Status_CL','Status_D']]

# Display the first few rows of the submission DataFrame
print(submission_df.head())

# Save the submission file
submission_df.to_csv('submission_LGB_def_2.csv', index=False)


      id  Status_C  Status_CL  Status_D
0  15000  0.801818   0.007106  0.191076
1  15001  0.631890   0.004465  0.363646
2  15002  0.987764   0.002702  0.009533
3  15003  0.163579   0.769440  0.066981
4  15004  0.214763   0.000833  0.784405
